In [1]:
import pandas as pd
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split, GridSearchCV
from xgboost import XGBClassifier
from joblib import dump

In [2]:
df_data = pd.read_csv('EGFR_Feature_Extraction.csv')
df_data.head()

molecule_chembl_id                                   canonical_smiles  \
0        CHEMBL68920  Cc1cc(C)c(/C=C2\C(=O)Nc3ncnc(Nc4ccc(F)c(Cl)c4)...   
1       CHEMBL137635        CN(c1ccccc1)c1ncnc2ccc(N/N=N/Cc3ccccn3)cc12   
2       CHEMBL306988             CC(=C(C#N)C#N)c1ccc(NC(=O)CCC(=O)O)cc1   
3        CHEMBL66879                             O=C(O)/C=C/c1ccc(O)cc1   
4        CHEMBL77085                 N#CC(C#N)=Cc1cc(O)ccc1[N+](=O)[O-]   

   Molecular Weight  Number of Rotatable Bonds  Number of Atoms  \
0        383.094916                          3               27   
1        369.170194                          6               28   
2        283.095691                          5               21   
3        164.047344                          2               12   
4        215.033091                          2               16   

   Number of Bonds  Count of Chiral Centers  Number of Rings  \
0               30                        0                4   
1               31                        0                4   
2               21                        0                1   
3               12                        0                1   
4               16                        0                1   

   Number of Aromatic Rings  Number of Hydrogen Bond Donors  \
0                         3                               3   
1                         4                               1   
2                         1                               2   
3                         1                               2   
4                         1                               1   

   Number of Hydrogen Bond Acceptors  Balaban J Index  Wiener Index     LogP  \
0                                  4         1.789174        1832.0  4.45034   
1                                  6         1.558763        2326.0  4.77200   
2                                  4         2.782020        1108.0  2.31056   
3                                  2         2.772026         223.0  1.49000   
4                                  5         3.386653         441.0  1.73096   

     TPSA  standard_value     class  
0   82.70            41.0    active  
1   78.66          9300.0  inactive  
2  113.98        500000.0  inactive  
3   57.53       3000000.0  inactive  
4  110.95         96000.0  inactive

In [3]:
df = df_data.drop(df_data.columns[-2], axis=1, inplace=True)
df = df_data.iloc[:, 2:]
print("Null values: " + str(df.isnull().values.any()))
print(df['class'].value_counts())
df.head()

Null values: False
class
active      3810
inactive    3524
Name: count, dtype: int64


Molecular Weight  Number of Rotatable Bonds  Number of Atoms  \
0        383.094916                          3               27   
1        369.170194                          6               28   
2        283.095691                          5               21   
3        164.047344                          2               12   
4        215.033091                          2               16   

   Number of Bonds  Count of Chiral Centers  Number of Rings  \
0               30                        0                4   
1               31                        0                4   
2               21                        0                1   
3               12                        0                1   
4               16                        0                1   

   Number of Aromatic Rings  Number of Hydrogen Bond Donors  \
0                         3                               3   
1                         4                               1   
2                         1                               2   
3                         1                               2   
4                         1                               1   

   Number of Hydrogen Bond Acceptors  Balaban J Index  Wiener Index     LogP  \
0                                  4         1.789174        1832.0  4.45034   
1                                  6         1.558763        2326.0  4.77200   
2                                  4         2.782020        1108.0  2.31056   
3                                  2         2.772026         223.0  1.49000   
4                                  5         3.386653         441.0  1.73096   

     TPSA     class  
0   82.70    active  
1   78.66  inactive  
2  113.98  inactive  
3   57.53  inactive  
4  110.95  inactive

In [4]:
X = df.iloc[:, :-1]
y = df.iloc[:, -1]

In [5]:
le = LabelEncoder()
y = le.fit_transform(y)

In [6]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.25, random_state=42)
eval_set = [(X_train, y_train), (X_test, y_test)]

In [7]:
param_grid = {
    'n_estimators': [500, 700], # Between 100 and 1000
    'max_depth': [6, 8], # Between 3 and 10
    'learning_rate': [0.3, 0.5], # Between 0.01 and 0.5
    'subsample': [0.8, 1.0], # Between 0.6 and 1.0
    'colsample_bytree': [0.8, 1.0], # Between 0.6 and 1.0
}

In [8]:
xgb = XGBClassifier()
xgb_grid_search = GridSearchCV(estimator=xgb, param_grid=param_grid, scoring='accuracy', n_jobs=-1, cv=5)
xgb_grid_search.fit(
    X_train,
    y_train,
    eval_set=eval_set,
)

[0]	validation_0-logloss:0.62456	validation_1-logloss:0.63093
[0]	validation_0-logloss:0.62564	validation_1-logloss:0.63088
[1]	validation_0-logloss:0.58180	validation_1-logloss:0.59355
[1]	validation_0-logloss:0.58212	validation_1-logloss:0.59378
[2]	validation_0-logloss:0.54719	validation_1-logloss:0.56902
[2]	validation_0-logloss:0.54865	validation_1-logloss:0.56454
[3]	validation_0-logloss:0.52450	validation_1-logloss:0.55260
[3]	validation_0-logloss:0.51681	validation_1-logloss:0.54129
[0]	validation_0-logloss:0.62701	validation_1-logloss:0.62938[4]	validation_0-logloss:0.50975	validation_1-logloss:0.54029

[4]	validation_0-logloss:0.49871	validation_1-logloss:0.52875
[5]	validation_0-logloss:0.48611	validation_1-logloss:0.52141
[5]	validation_0-logloss:0.49007	validation_1-logloss:0.52474
[1]	validation_0-logloss:0.58069	validation_1-logloss:0.59160
[6]	validation_0-logloss:0.47004	validation_1-logloss:0.51285
[0]	validation_0-logloss:0.62431	validation_1-logloss:0.63124
[2]	vali

GridSearchCV(cv=5,
             estimator=XGBClassifier(base_score=None, booster=None,
                                     callbacks=None, colsample_bylevel=None,
                                     colsample_bynode=None,
                                     colsample_bytree=None, device=None,
                                     early_stopping_rounds=None,
                                     enable_categorical=False, eval_metric=None,
                                     feature_types=None, gamma=None,
                                     grow_policy=None, importance_type=None,
                                     interaction_constraints=None,
                                     learning_rate=None,...
                                     max_delta_step=None, max_depth=None,
                                     max_leaves=None, min_child_weight=None,
                                     missing=nan, monotone_constraints=None,
                                     multi_strategy=None, n_estimators=None,
                                     n_jobs=None, num_parallel_tree=None,
                                     random_state=None, ...),
             n_jobs=-1,
             param_grid={'colsample_bytree': [0.8, 1.0],
                         'learning_rate': [0.3, 0.5], 'max_depth': [6, 8],
                         'n_estimators': [500, 700], 'subsample': [0.8, 1.0]},
             scoring='accuracy')

In [9]:
print("Best parameters found: ", xgb_grid_search.best_params_)
print("Best cross-validation score: {:.2f}".format(xgb_grid_search.best_score_))

Best parameters found:  {'colsample_bytree': 0.8, 'learning_rate': 0.3, 'max_depth': 8, 'n_estimators': 700, 'subsample': 1.0}
Best cross-validation score: 0.82


In [10]:
best_model = xgb_grid_search.best_estimator_
test_accuracy = best_model.score(X_test, y_test)
print("Test set accuracy: {:.2f}".format(test_accuracy))

Test set accuracy: 0.82


In [11]:
saved_model = 'MainXGBRFClassifier.joblib'
dump(best_model, saved_model)

['MainXGBRFClassifier.joblib']